In [1]:
bronze_location = "abfss://bronze@prsynapselab.dfs.core.windows.net/"
write_mode="append"


StatementMeta(prmadisp, 26, 1, Finished, Available)

In [2]:
claimSchema = spark.read.json(bronze_location+"historic_data/claim/year=2016/part-00000-6650129e-31bc-4bc3-9443-0c6529438b3d.c000.json").schema
claim_df = spark.read.schema(claimSchema).json(bronze_location+"incremental_data/claim/*/*/*/*.json")

StatementMeta(prmadisp, 26, 2, Finished, Available)

In [3]:
claim_df.printSchema()

StatementMeta(prmadisp, 26, 3, Finished, Available)

root
 |-- billablePeriod: struct (nullable = true)
 |    |-- end: string (nullable = true)
 |    |-- start: string (nullable = true)
 |-- created: string (nullable = true)
 |-- diagnosis: array (nullable = true)
 |    |-- element: struct (containsNull = true)
 |    |    |-- diagnosisReference: struct (nullable = true)
 |    |    |    |-- reference: string (nullable = true)
 |    |    |-- sequence: long (nullable = true)
 |-- id: string (nullable = true)
 |-- insurance: array (nullable = true)
 |    |-- element: struct (containsNull = true)
 |    |    |-- coverage: struct (nullable = true)
 |    |    |    |-- display: string (nullable = true)
 |    |    |-- focal: boolean (nullable = true)
 |    |    |-- sequence: long (nullable = true)
 |-- item: array (nullable = true)
 |    |-- element: struct (containsNull = true)
 |    |    |-- diagnosisSequence: array (nullable = true)
 |    |    |    |-- element: long (containsNull = true)
 |    |    |-- encounter: array (nullable = true)
 |    |

In [4]:
display(claim_df)

StatementMeta(prmadisp, 26, 4, Finished, Available)

SynapseWidget(Synapse.DataFrame, 1bf38b1a-dfd1-47e9-b488-4e518fa47f4e)

In [5]:
claim_df_selected = claim_df.select("id","resourceType","status","billablePeriod","created","patient","prescription","provider","total","use","insurance","diagnosis","procedure") \
                        .toDF(*("claim_id","resourceType","status","billablePeriod","created","patient","prescription","provider","total","isuse","insurance","diagnosis","procedure"))

StatementMeta(prmadisp, 26, 5, Finished, Available)

In [6]:
claim_df_selected.createOrReplaceTempView("claim_df_selected")

StatementMeta(prmadisp, 26, 6, Finished, Available)

In [7]:
%%spark
import org.apache.spark.sql.types.{StructType,ArrayType}
import org.apache.spark.sql.DataFrame
import org.apache.spark.sql.Column
import org.apache.spark.sql.functions.col
import org.apache.spark.sql.functions.explode_outer

def flattenDataFrame(df: DataFrame): DataFrame = {
  val fields = df.schema.fields
  val fieldNames = fields.map(x => x.name)

  for (i <- fields.indices) {
    val field = fields(i)
    val fieldType = field.dataType
    val fieldName = field.name
    fieldType match {
      case _: ArrayType =>
        val fieldNamesExcludingArray = fieldNames.filter(_ != fieldName)
        val fieldNamesAndExplode = fieldNamesExcludingArray ++ Array(
          s"explode_outer($fieldName) as $fieldName"
        )
        val explodedDf = df.selectExpr(fieldNamesAndExplode: _*)
        return flattenDataFrame(explodedDf)
      case structType: StructType =>
        val childFieldNames =
          structType.fieldNames.map(childname => fieldName + "." + childname)
        val newFieldNames = fieldNames.filter(_ != fieldName) ++ childFieldNames
        import org.apache.spark.sql.functions.col

        val renamedCols =
          newFieldNames.map { x =>
            col(x.toString).as(x.toString.replace(".", "_"))
          }

        val explodedDf = df.select(renamedCols: _*)
        return flattenDataFrame(explodedDf)
      case _ =>
    }
  }

  df
}

StatementMeta(prmadisp, 26, 8, Finished, Available)

import org.apache.spark.sql.types.{StructType, ArrayType}
import org.apache.spark.sql.DataFrame
import org.apache.spark.sql.Column
import org.apache.spark.sql.functions.col
import org.apache.spark.sql.functions.explode_outer
flattenDataFrame: (df: org.apache.spark.sql.DataFrame)org.apache.spark.sql.DataFrame


## Creating Claim Main Table

In [8]:
claim_df_selected.printSchema()

StatementMeta(prmadisp, 26, 9, Finished, Available)

root
 |-- claim_id: string (nullable = true)
 |-- resourceType: string (nullable = true)
 |-- status: string (nullable = true)
 |-- billablePeriod: struct (nullable = true)
 |    |-- end: string (nullable = true)
 |    |-- start: string (nullable = true)
 |-- created: string (nullable = true)
 |-- patient: struct (nullable = true)
 |    |-- display: string (nullable = true)
 |    |-- reference: string (nullable = true)
 |-- prescription: struct (nullable = true)
 |    |-- reference: string (nullable = true)
 |-- provider: struct (nullable = true)
 |    |-- display: string (nullable = true)
 |    |-- reference: string (nullable = true)
 |-- total: struct (nullable = true)
 |    |-- currency: string (nullable = true)
 |    |-- value: double (nullable = true)
 |-- isuse: string (nullable = true)
 |-- insurance: array (nullable = true)
 |    |-- element: struct (containsNull = true)
 |    |    |-- coverage: struct (nullable = true)
 |    |    |    |-- display: string (nullable = true)
 |  

In [9]:
%%spark
val claim_main_df = spark.sql("select * from claim_df_selected").drop("insurance","diagnosis","procedure");


StatementMeta(prmadisp, 26, 10, Finished, Available)

claim_main_df: org.apache.spark.sql.DataFrame = [claim_id: string, resourceType: string ... 8 more fields]


In [10]:
%%spark
val claim_main_df_flattened = flattenDataFrame(claim_main_df)

StatementMeta(prmadisp, 26, 11, Finished, Available)

claim_main_df_flattened: org.apache.spark.sql.DataFrame = [claim_id: string, resourceType: string ... 12 more fields]


In [11]:
%%spark
display(claim_main_df_flattened)

StatementMeta(prmadisp, 26, 12, Finished, Available)

SynapseWidget(Synapse.DataFrame, edb14149-c3eb-4702-a4d7-11b1d9476b6b)

In [12]:
%%spark
val silver_location = "abfss://silver@prsynapselab.dfs.core.windows.net/"
val write_mode="append"
claim_main_df_flattened.coalesce(200).write.format("delta").option("path", silver_location+"claim_main").mode(write_mode).saveAsTable("fhir.claim_main_hash")


StatementMeta(prmadisp, 26, 13, Finished, Available)

silver_location: String = abfss://silver@prsynapselab.dfs.core.windows.net/
write_mode: String = append


## Creating Claim Insurance Table

In [13]:
%%spark
val claim_insurance_df = spark.sql("select claim_id, insurance from claim_df_selected")
val claim_insurance_df_flattened = flattenDataFrame(claim_insurance_df)
display(claim_insurance_df_flattened)

StatementMeta(prmadisp, 26, 14, Finished, Available)

SynapseWidget(Synapse.DataFrame, 816e9435-9ae3-4078-ae36-fac621a45774)


claim_insurance_df: org.apache.spark.sql.DataFrame = [claim_id: string, insurance: array<struct<coverage:struct<display:string>,focal:boolean,sequence:bigint>>]
claim_insurance_df_flattened: org.apache.spark.sql.DataFrame = [claim_id: string, insurance_focal: boolean ... 2 more fields]


In [14]:
%%spark
val silver_location = "abfss://silver@prsynapselab.dfs.core.windows.net/"
val write_mode="append"
claim_insurance_df_flattened.coalesce(200).write.format("delta").option("path", silver_location+"claim_insurance").mode(write_mode).saveAsTable("fhir.claim_insurance_hash")

StatementMeta(prmadisp, 26, 15, Finished, Available)

silver_location: String = abfss://silver@prsynapselab.dfs.core.windows.net/
write_mode: String = append


## Creating Claim Diagnosis Table

In [15]:
%%spark
val claim_diagnosis_df = spark.sql("select claim_id, diagnosis from claim_df_selected")
val claim_diagnosis_df_flattened = flattenDataFrame(claim_diagnosis_df)
display(claim_diagnosis_df_flattened)

StatementMeta(prmadisp, 26, 16, Finished, Available)

SynapseWidget(Synapse.DataFrame, f0b7c6af-dda8-48c8-8883-f91d67b4b14c)


claim_diagnosis_df: org.apache.spark.sql.DataFrame = [claim_id: string, diagnosis: array<struct<diagnosisReference:struct<reference:string>,sequence:bigint>>]
claim_diagnosis_df_flattened: org.apache.spark.sql.DataFrame = [claim_id: string, diagnosis_sequence: bigint ... 1 more field]


In [16]:
%%spark
val silver_location = "abfss://silver@prsynapselab.dfs.core.windows.net/"
val write_mode="append"
claim_diagnosis_df_flattened.coalesce(200).write.format("delta").option("path", silver_location+"claim_diagnosis").mode(write_mode).saveAsTable("fhir.claim_diagnosis_hash")

StatementMeta(prmadisp, 26, 17, Finished, Available)

silver_location: String = abfss://silver@prsynapselab.dfs.core.windows.net/
write_mode: String = append


## Creating Claim procedure Table

In [17]:
%%spark
val claim_procedure_df = spark.sql("select claim_id, procedure from claim_df_selected")
val claim_procedure_df_flattened = flattenDataFrame(claim_procedure_df)
display(claim_procedure_df_flattened)

StatementMeta(prmadisp, 26, 18, Finished, Available)

SynapseWidget(Synapse.DataFrame, aad2e717-b09c-4ff8-a2be-058491e850bd)


claim_procedure_df: org.apache.spark.sql.DataFrame = [claim_id: string, procedure: array<struct<procedureReference:struct<reference:string>,sequence:bigint>>]
claim_procedure_df_flattened: org.apache.spark.sql.DataFrame = [claim_id: string, procedure_sequence: bigint ... 1 more field]


In [18]:
%%spark
val silver_location = "abfss://silver@prsynapselab.dfs.core.windows.net/"
val write_mode="append"
claim_procedure_df_flattened.coalesce(200).write.format("delta").option("path", silver_location+"claim_procedure").mode(write_mode).saveAsTable("fhir.claim_procedure_hash")

StatementMeta(prmadisp, 26, 19, Finished, Available)

silver_location: String = abfss://silver@prsynapselab.dfs.core.windows.net/
write_mode: String = append
